# Spatial interpolation

In your life as a spatial data scientist, you will find yourself in a
situation where you have plenty of data to work with, just linked to
different geometries or representing slightly different locations that
you need. When this happens, you need to *interpolate* the data from one
set of geometries, on which the data is shipped, to the other, the one
you are interested in.

Any interpolation method is necessarily an approximation but some are
better than others.

In [2]:
import geopandas as gpd
import tobler
import pyinterpolate
import numpy as np
import matplotlib.pyplot as plt

from libpysal import graph
from sklearn import neighbors
from scipy import interpolate

This chapter of the course covers two types of interpolation - from one
set of polygons to another set of polygons, and from a sparse set of
points to other locations in the same area.

## Areal interpolation and dasymetric mapping

The first use case is the interpolation of data from one set of
geometries to the other one, otherwise known as *areal interpolation* or
*dasymetric mapping*.

### Data zones and H3

You are already familiar with the Scottish Index of Multiple
Deprivation, so let’s use it as an example of areal interpolation. Load
the subset of SIMD 2020 for the City of Edinburgh.

In [3]:
simd = gpd.read_file(
    "https://martinfleischmann.net/sds/interpolation/data/edinburgh_simd_2020.gpkg"
)
simd.head(2)

2 rows × 52 columns

> **Alternative**
>
> Instead of reading the file directly off the web, it is possible to
> download it manually, store it on your computer, and read it locally.
> To do that, you can follow these steps:
>
> 1.  Download the file by right-clicking on [this
>     link](https://martinfleischmann.net/sds/interpolation/data/edinburgh_simd_2020.gpkg)
>     and saving the file
> 2.  Place the file in the same folder as the notebook where you intend
>     to read it
> 3.  Replace the code in the cell above with:
>
> ``` python
> simd = gpd.read_file(
>     "edinburgh_simd_2020.gpkg",
> )
> ```

Get an interactive map with one of the variables to get more familiar
with the data.

In [4]:
simd[["EmpNumDep", "geometry"]].explore("EmpNumDep", tiles="CartoDB Positron")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_46cdcaddd3ed5a2ebe5b104c0dbb5d98 {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js"></script>
</head>
<body>
 
 
 <div class="folium-map" id="map_46cdcaddd3ed5a2ebe5b104c0dbb5d98" ></div>
 
</body>
<script>
 
 
 var map_46cdcaddd3ed5a2ebe5b104c0dbb5d98 = L.map(
 "map_46cdcaddd3ed5a2ebe5b104c0dbb5d98",
 {
 center: [55.91548084724146, -3.2636050528061906],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_46cdcaddd3ed5a2ebe5b104c0dbb5d98);

 

 
 
 var tile_layer_7672c135ac8311933ab323fff4d49458 = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_7672c135ac8311933ab323fff4d49458.addTo(map_46cdcaddd3ed5a2ebe5b104c0dbb5d98);
 
 
 map_46cdcaddd3ed5a2ebe5b104c0dbb5d98.fitBounds(
 [[55.818791345760204, -3.4495294825265796], [56.01217034872272, -3.077680623085801]],
 {}
 );
 
 
 function geo_json_4a7ceafdaa3563c843fb1784f98694d9_styler(feature) {
 switch(feature.id) {
 case "0": case "6": case "12": case "21": case "86": case "93": case "170": case "192": case "198": case "221": case "230": case "249": case "279": case "414": case "495": case "498": case "529": 
 return {"color": "#481467", "fillColor": "#481467", "fillOpacity": 0.5, "weight": 2};
 case "1": case "3": case "10": case "88": case "101": case "102": case "104": case "117": case "190": case "213": case "223": case "281": case "283": case "328": case "333": case "415": case "428": case "437": case "441": case "447": case "467": case "481": case "527": case "554": 
 return {"color": "#460b5e", "fillColor": "#460b5e", "fillOpacity": 0.5, "weight": 2};
 case "2": case "52": case "174": case "185": case "197": case "211": case "254": cas

This is the source - data linked to SIMD Data Zones. Let’s now focus on
the target geometries. Popular spatial units of analysis are hexagonal
grids and Uber’s hierarchical H3 grid especially.

> **More on H3**
>
> H3 grids are a very interesting concept as they often allow for very
> efficient spatial operations based on known relationships between
> individual cells (encoded in their index). Check the [official
> documentation](https://h3geo.org) if you want to learn more.

You can create the H3 grid covering the area of Edinburgh using the
`tobler` package.

In [5]:
grid_8 = tobler.util.h3fy(simd, resolution=8)
grid_8.head(2)

/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/pyproj/crs/crs.py:1293: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  proj = self._crs.to_proj4(version=version)

Let’s check how the H3 grid overlaps the data zones of SIMD.

In [6]:
m = simd.boundary.explore(tiles="CartoDB Positron")
grid_8.boundary.explore(m=m, color="red")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_8ef8c4e29049d2c11e31b3e334217e9f {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
</head>
<body>
 
 
 <div class="folium-map" id="map_8ef8c4e29049d2c11e31b3e334217e9f" ></div>
 
</body>
<script>
 
 
 var map_8ef8c4e29049d2c11e31b3e334217e9f = L.map(
 "map_8ef8c4e29049d2c11e31b3e334217e9f",
 {
 center: [55.91548084724146, -3.2636050528061906],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_8ef8c4e29049d2c11e31b3e334217e9f);

 

 
 
 var tile_layer_d1c30cd475161cd5eee5277967221458 = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_d1c30cd475161cd5eee5277967221458.addTo(map_8ef8c4e29049d2c11e31b3e334217e9f);
 
 
 map_8ef8c4e29049d2c11e31b3e334217e9f.fitBounds(
 [[55.818791345760204, -3.4495294825265796], [56.01217034872272, -3.077680623085801]],
 {}
 );
 
 
 function geo_json_39d6e98b5b1cba174ad6099ed6c59c17_styler(feature) {
 switch(feature.id) {
 default:
 return {"fillOpacity": 0.5, "weight": 2};
 }
 }
 function geo_json_39d6e98b5b1cba174ad6099ed6c59c17_highlighter(feature) {
 switch(feature.id) {
 default:
 return {"fillOpacity": 0.75};
 }
 }
 function geo_json_39d6e98b5b1cba174ad6099ed6c59c17_pointToLayer(feature, latlng) {
 var opts = {"bubblingMouseEvents": true, "color": "#3388ff", "dashArray": null, "dashOffset": null, "fill": true, "fillColor": "#3388ff", "fillOpacity": 0.2, "fillRule": "evenodd", "lineCap": "round", "lineJoin": "round", "opacity": 1.0, "radius": 2, "stroke": true, "weight": 3};
 
 let style = geo_json_39d6e98b5b1cba174ad6099ed6c59c17_styler(feat

Some grid cells are fully within a data zone geometry, some data zones
are fully within a single grid cell but overall, there is a lot of
partial overlap.

### tobler and Tobler

The task ahead can be done in many ways falling under the umbrella of
dasymetric mapping. PySAL has a package designed for areal interpolation
called `tobler`. You have already used it to create the H3 grid but that
is only a small utility function included in `tobler`. The name of the
package is a homage to the Waldo R. Tobler, a famous geographer and an
author of a Pycnophylactic interpolation covered below

### Simple areal interpolation

But before getting to the Pycnophylactic interpolation, let’s start with
the simple case of basic areal interpolation. The logic behind it is
quite simple - the method redistributes values from the source
geometries to target geometries based on the proportion of area that is
shared between each source polygon and each target polygon. It is not a
simple join as you would get with `sjoin()` or `overlay()` methods from
`geopandas` but it is not far from it. Areal interpolation brings an
additional step of taking the values and redistributing them instead of
merging. That means that if the source geometry contains a count of 10
people and 40% of the geometry is covered by a target polygon A, 40% by
a target polygon B and 20% by a target polygon C, each gets a relevant
proportion of the original count (4, 4, and 2). Similarly are treated
intensive variables (e.g. a percentage).

The function you need to use for this kind of areal interpolation lives
in the `area_weighted` module of `tobler` and is called simply
`area_interpolate`. Use it to interpolate a subset of data from `simd`
to `grid_8`.

In [7]:
interpolated = tobler.area_weighted.area_interpolate(
    source_df=simd,
    target_df=grid_8,
    extensive_variables=["EmpNumDep", "IncNumDep"],
    intensive_variables=["EmpRate", "IncRate"],
)
interpolated.head(2)

The resulting `interpolated` `GeoDataFrame` contains the selected
variables from `simd` but linked to the `grid_8` geometries. You can
check the result on a map and compare it to the one above.

In [8]:
interpolated.explore("EmpNumDep", tiles="CartoDB Positron")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_6a65b8fcbfb0002ebb1c498491a19183 {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js"></script>
</head>
<body>
 
 
 <div class="folium-map" id="map_6a65b8fcbfb0002ebb1c498491a19183" ></div>
 
</body>
<script>
 
 
 var map_6a65b8fcbfb0002ebb1c498491a19183 = L.map(
 "map_6a65b8fcbfb0002ebb1c498491a19183",
 {
 center: [55.911620089332004, -3.2651690979931915],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_6a65b8fcbfb0002ebb1c498491a19183);

 

 
 
 var tile_layer_931d53671a4a75881292aceb2e43bcf4 = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_931d53671a4a75881292aceb2e43bcf4.addTo(map_6a65b8fcbfb0002ebb1c498491a19183);
 
 
 map_6a65b8fcbfb0002ebb1c498491a19183.fitBounds(
 [[55.82084390326666, -3.452142523292945], [56.00239627539734, -3.078195672693438]],
 {}
 );
 
 
 function geo_json_86ab6421766c2b7fe69e742be039152d_styler(feature) {
 switch(feature.id) {
 case "0": 
 return {"color": "#a8db34", "fillColor": "#a8db34", "fillOpacity": 0.5, "weight": 2};
 case "1": case "34": case "40": case "43": case "55": case "107": case "109": case "118": case "129": case "146": case "158": case "204": case "211": case "225": case "227": case "256": case "276": case "329": case "389": case "400": case "402": 
 return {"color": "#440256", "fillColor": "#440256", "fillOpacity": 0.5, "weight": 2};
 case "2": case "4": case "5": case "7": case "10": case "11": case "17": case "22": case "26": case "27": case "29": case "30": case "31": case "32": case "33": case "37": case "39": case "41": case "42": case "44": case "45": case "48": case "49": case "50": case "51": case "52": case "54": case "56": cas

> **Raster masking**
>
> You may have noticed that even if the actual location where a grid
> cell lies does not contain any buildings, it gets a proportion of data
> based on the area of overlap. That may not be an issue in some cases
> but if you want to be more precise, you can use a raster layer as a
> mask to further influence the redistribution of values. See the
> [documentation](https://pysal.org/tobler/notebooks/01_interpolation_methods_overview.html#Model-Based-Interpolation)
> for details.

### Pycnophylactic interpolation

Another option is to use Pycnophylactic interpolation
\[@tobler1979smooth\], a method that creates a smooth contour map of the
original data while preserving the volume but avoiding sharp boundaries
and uses this to interpolate values onto the target polygons. Unlike
`area_interpolate`, `pycno_interpolate` does not handle intensive
variables.

In [9]:
pycno_8 = tobler.pycno.pycno_interpolate(
    source_df=simd,
    target_df=grid_8,
    variables=["EmpNumDep", "IncNumDep"],
    cellsize=200,
)

/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:134: RuntimeWarning: divide by zero encountered in scalar divide
  correct = (val - nansum(data[mask])) / mask.sum()
/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:145: RuntimeWarning: divide by zero encountered in scalar divide
  correct = val / nansum(data[mask])
/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:134: RuntimeWarning: divide by zero encountered in scalar divide
  correct = (val - nansum(data[mask])) / mask.sum()
/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:145: RuntimeWarning: divide by zero encountered in scalar divide
  correct = val / nansum(data[mask])
/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:145: RuntimeWarning: invalid value encountered in scalar divide
  correct = val / nansum(data[mask])

From the user perspective, both `area_interpolate` and
`pycno_interpolate` look similar but the results will likely differ.

In [10]:
pycno_8.explore("EmpNumDep", tiles="CartoDB Positron")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_d8eb6fc53c821992875d10704c512fd2 {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js"></script>
</head>
<body>
 
 
 <div class="folium-map" id="map_d8eb6fc53c821992875d10704c512fd2" ></div>
 
</body>
<script>
 
 
 var map_d8eb6fc53c821992875d10704c512fd2 = L.map(
 "map_d8eb6fc53c821992875d10704c512fd2",
 {
 center: [55.911620089332004, -3.2651690979931915],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_d8eb6fc53c821992875d10704c512fd2);

 

 
 
 var tile_layer_9c0e7727679e17a81c465e56e021fe8b = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_9c0e7727679e17a81c465e56e021fe8b.addTo(map_d8eb6fc53c821992875d10704c512fd2);
 
 
 map_d8eb6fc53c821992875d10704c512fd2.fitBounds(
 [[55.82084390326666, -3.452142523292945], [56.00239627539734, -3.078195672693438]],
 {}
 );
 
 
 function geo_json_9829e3bec13b82ba9583beae4636f003_styler(feature) {
 switch(feature.id) {
 case "0": 
 return {"color": "#5cc863", "fillColor": "#5cc863", "fillOpacity": 0.5, "weight": 2};
 case "1": case "2": case "4": case "5": case "7": case "10": case "11": case "17": case "19": case "22": case "26": case "27": case "29": case "30": case "31": case "32": case "33": case "34": case "37": case "39": case "41": case "42": case "43": case "44": case "45": case "48": case "49": case "50": case "51": case "52": case "53": case "54": case "55": case "56": case "59": case "62": case "64": case "66": case "67": case "68": case "69": case "70": case "71": case "72": case "74": case "83": case "85": case "88": case "89": case "90": case "92": case "94": case "99": case "101": case "102": case "103": case "104": case "108": case

For a better understanding of the method, you can look at the
intermediate array of smoothed values by accessing the `pycno` function
from the depth of the `tobler.pycno` module.

In [11]:
arr, _, _ = tobler.pycno.pycno.pycno(
    gdf=simd, value_field="EmpNumDep", cellsize=200, verbose=False
)

/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:134: RuntimeWarning: divide by zero encountered in scalar divide
  correct = (val - nansum(data[mask])) / mask.sum()
/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/tobler/pycno/pycno.py:145: RuntimeWarning: divide by zero encountered in scalar divide
  correct = val / nansum(data[mask])

The function returns a numpy array of smoothed values and two pieces of
information related to CRS, that are not relevant here. The array itself
can be explored directly using `matplotlib`:

In [12]:
_ = plt.imshow(arr)

> **Theory behind**
>
> For more details on the theory behind both areal and Pycnophylactic
> interpolation methods, check [this
> resource](https://gistbok.ucgis.org/bok-topics/2022-quarter-04/areal-interpolation)
> by @comber2022areal.

## Point interpolation

Another case of *interpolation* is an interpolation of values from a
sparse set of points to any other location in between. Let’s explore our
options based on the Airbnb data in Edinburgh.

### Airbnb in Edinburgh

You are already familiar with the Airbnb data from the [Is there a
pattern?](../point_patterns/exercise.qmd) exercise. The dataset for
Edinburgh looks just like that for Prague you used before. The only
difference is that, for this section, it is pre-processed to create
geometry and remove unnecessary columns.

In [13]:
airbnb = gpd.read_file(
    "https://martinfleischmann.net/sds/interpolation/data/edinburgh_airbnb_2023.gpkg"
)
airbnb.head()

> **Alternative**
>
> Instead of reading the file directly off the web, it is possible to
> download it manually, store it on your computer, and read it locally.
> To do that, you can follow these steps:
>
> 1.  Download the file by right-clicking on [this
>     link](https://martinfleischmann.net/sds/interpolation/data/edinburgh_airbnb_2023.gpkg)
>     and saving the file
> 2.  Place the file in the same folder as the notebook where you intend
>     to read it
> 3.  Replace the code in the cell above with:
>
> ``` python
> airbnb = gpd.read_file(
>     "edinburgh_airbnb_2023.gpkg",
> )
> ```

You will be focusing on the price of each listing. Let’s check that
column.

In [14]:
airbnb.price.head()

0    $126.00
1    $269.00
2     $95.00
3    $172.00
4    $361.00
Name: price, dtype: object

While the values represent numbers, they are encoded as strings starting
with the `$` sign. That will not work for any interpolation (or any
other mathematical method). Use `pandas` to strip the string of the `$`
character, remove `,` and cast the remaining to `float`.

In [15]:
airbnb["price_float"] = (
    airbnb.price.str.strip("$").str.replace(",", "").astype(float)
)

That is set now, you have numbers as expected. Since the dataset
represents all types of Airbnb listings, it may be better to select only
one type. Filter out only those with 2 bedrooms that can be rented as
the whole flat and have a price under £300 per night (there are some
crazy outliers).

In [16]:
two_bed_homes = airbnb[
    (airbnb["bedrooms"] == 2)
    & (airbnb["property_type"] == "Entire rental unit")
    & (airbnb["price_float"] < 300)
].copy()
two_bed_homes.head()

Another useful check before heading to the land of interpolation is for
duplicated geometries. Having two points at the same place, each with a
different value could lead to unexpected results.

In [17]:
two_bed_homes.geometry.duplicated().any()

True

There are some duplicated geometries. Let’s simply drop rows with
duplicated locations and keep only the first occurrence (the default
behaviour of `drop_duplicates`).

In [18]:
two_bed_homes = two_bed_homes.drop_duplicates("geometry")

Check how the cleaned result looks on a map.

In [19]:
two_bed_homes.explore("price_float", tiles="CartoDB Positron")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_2bb65a8345b6e70d5ed46a8a41f2a09c {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js"></script>
</head>
<body>
 
 
 <div class="folium-map" id="map_2bb65a8345b6e70d5ed46a8a41f2a09c" ></div>
 
</body>
<script>
 
 
 var map_2bb65a8345b6e70d5ed46a8a41f2a09c = L.map(
 "map_2bb65a8345b6e70d5ed46a8a41f2a09c",
 {
 center: [55.937265, -3.2510422245910693],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_2bb65a8345b6e70d5ed46a8a41f2a09c);

 

 
 
 var tile_layer_409fddcc9a5454f843deac1678af190d = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_409fddcc9a5454f843deac1678af190d.addTo(map_2bb65a8345b6e70d5ed46a8a41f2a09c);
 
 
 map_2bb65a8345b6e70d5ed46a8a41f2a09c.fitBounds(
 [[55.88358, -3.407260000000005], [55.99095, -3.094824449182134]],
 {}
 );
 
 
 function geo_json_1d4912ff4d5e978ab9ee3e496a828912_styler(feature) {
 switch(feature.id) {
 case "3": case "1366": case "1396": case "2268": case "3932": case "3979": case "6882": case "7054": 
 return {"color": "#1f958b", "fillColor": "#1f958b", "fillOpacity": 0.5, "weight": 2};
 case "5": case "53": case "549": case "5632": 
 return {"color": "#aadc32", "fillColor": "#aadc32", "fillOpacity": 0.5, "weight": 2};
 case "6": case "1375": case "7551": case "7562": 
 return {"color": "#1f9a8a", "fillColor": "#1f9a8a", "fillOpacity": 0.5, "weight": 2};
 case "10": case "562": case "630": case "972": case "1931": case "3381": case "3637": case "6192": case "7009": case "7152": 
 return {"color": "#23888e", "fillColor": "#23888e", "fillOpacity": 0.5, "weight": 2};
 case "17": case "255": case "1490": case "2596": case "3166": case "5204": case "7048": cas

There are some visible patterns of higher and lower prices, but it may
be tricky to do interpolation since the data is a bit too chaotic. In
general, point interpolation methods work only when there is a spatial
autocorrelation in the data and stronger autocorrelation leads to better
interpolation. As you know, spatially lagged variable of already
autocorrelated variable shows higher levels of autocorrelation, hence
using the spatial lag will be beneficial for this section.

In [20]:
knn = graph.Graph.build_kernel(two_bed_homes, k=10).transform("r")
two_bed_homes["price_lag"] = knn.lag(two_bed_homes.price_float)
two_bed_homes.explore("price_lag", tiles="CartoDB Positron")

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe srcdoc="<!DOCTYPE html>
<html>
<head>
 
 <meta http-equiv="content-type" content="text/html; charset=UTF-8" />
 
 <script>
 L_NO_TOUCH = false;
 L_DISABLE_3D = false;
 </script>
 
 <style>html, body {width: 100%;height: 100%;margin: 0;padding: 0;}</style>
 <style>#map {position:absolute;top:0;bottom:0;right:0;left:0;}</style>
 <script src="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.js"></script>
 <script src="https://code.jquery.com/jquery-3.7.1.min.js"></script>
 <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/js/bootstrap.bundle.min.js"></script>
 <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.9.3/dist/leaflet.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/bootstrap@5.2.2/dist/css/bootstrap.min.css"/>
 <link rel="stylesheet" href="https://netdna.bootstrapcdn.com/bootstrap/3.0.0/css/bootstrap-glyphicons.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/@fortawesome/fontawesome-free@6.2.0/css/all.min.css"/>
 <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css"/>
 <link rel="stylesheet" href="https://cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css"/>
 
 <meta name="viewport" content="width=device-width,
 initial-scale=1.0, maximum-scale=1.0, user-scalable=no" />
 <style>
 #map_2682bcf42cb2c16b38438ea7699e0278 {
 position: relative;
 width: 100.0%;
 height: 100.0%;
 left: 0.0%;
 top: 0.0%;
 }
 .leaflet-container { font-size: 1rem; }
 </style>
 
 
 <style>
 .foliumtooltip {
 
 }
 .foliumtooltip table{
 margin: auto;
 }
 .foliumtooltip tr{
 text-align: left;
 }
 .foliumtooltip th{
 padding: 2px; padding-right: 8px;
 }
 </style>
 
 <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js"></script>
</head>
<body>
 
 
 <div class="folium-map" id="map_2682bcf42cb2c16b38438ea7699e0278" ></div>
 
</body>
<script>
 
 
 var map_2682bcf42cb2c16b38438ea7699e0278 = L.map(
 "map_2682bcf42cb2c16b38438ea7699e0278",
 {
 center: [55.937265, -3.2510422245910693],
 crs: L.CRS.EPSG3857,
 zoom: 10,
 zoomControl: true,
 preferCanvas: false,
 }
 );
 L.control.scale().addTo(map_2682bcf42cb2c16b38438ea7699e0278);

 

 
 
 var tile_layer_bdae065c659fe33ccb5d73cc34bce51f = L.tileLayer(
 "https://a.basemaps.cartocdn.com/light_all/{z}/{x}/{y}{r}.png",
 {"attribution": "\u0026copy; \u003ca href=\"https://www.openstreetmap.org/copyright\"\u003eOpenStreetMap\u003c/a\u003e contributors \u0026copy; \u003ca href=\"https://carto.com/attributions\"\u003eCARTO\u003c/a\u003e", "detectRetina": false, "maxZoom": 20, "minZoom": 0, "noWrap": false, "opacity": 1, "subdomains": "abc", "tms": false}
 );
 
 
 tile_layer_bdae065c659fe33ccb5d73cc34bce51f.addTo(map_2682bcf42cb2c16b38438ea7699e0278);
 
 
 map_2682bcf42cb2c16b38438ea7699e0278.fitBounds(
 [[55.88358, -3.407260000000005], [55.99095, -3.094824449182134]],
 {}
 );
 
 
 function geo_json_779f6dfead9dda5739f1d2af8ae762b6_styler(feature) {
 switch(feature.id) {
 case "3": case "10": case "121": case "1455": case "2113": case "3026": case "7109": 
 return {"color": "#70cf57", "fillColor": "#70cf57", "fillOpacity": 0.5, "weight": 2};
 case "5": case "825": case "2267": case "3580": 
 return {"color": "#1e9c89", "fillColor": "#1e9c89", "fillOpacity": 0.5, "weight": 2};
 case "6": case "1071": case "1360": case "1449": case "2212": case "2568": case "3958": 
 return {"color": "#21908d", "fillColor": "#21908d", "fillOpacity": 0.5, "weight": 2};
 case "17": case "549": case "1325": 
 return {"color": "#aadc32", "fillColor": "#aadc32", "fillOpacity": 0.5, "weight": 2};
 case "19": case "258": case "746": case "1920": case "2194": case "2403": case "2424": case "2887": case "3242": case "4174": case "6945": case "7146": cas

This looks much better. Let’s start with some interpolation. Create
another H3 grid, this time with a resolution of 10 (much smaller cells
than before). You will use it as a target of interpolation.

In [21]:
grid_10 = tobler.util.h3fy(simd, resolution=10)

/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/pyproj/crs/crs.py:1293: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  proj = self._crs.to_proj4(version=version)

All of the methods below do not expect geometries as an input, but
arrays of coordinates. That is an easy task. An array from the grid can
be extracted from the centroid of each cell:

In [22]:
grid_coordinates = grid_10.centroid.get_coordinates()
grid_coordinates.head()

And an array from the Airbnb subset can be retrieved directly from point
data:

In [23]:
homes_coordinates = two_bed_homes.get_coordinates()
homes_coordinates.head()

### Nearest

The simplest case is the *nearest* interpolation. That assigns a value
to a given point based on the value of the nearest point in the original
dataset. You can use the `griddata` function from the
`scipy.interpolate` module to do that efficiently.

In [24]:
nearest = interpolate.griddata(
    points=homes_coordinates,
    values=two_bed_homes.price_lag,
    xi=grid_coordinates,
    method="nearest",
)
nearest

array([181.        ,  80.        ,  78.        , ..., 188.70398583,
       188.70398583,  84.        ])

The result is provided as a `numpy.ndarray` object aligned with
`grid_coordinates`, so you can directly assign it as a column.

In [25]:
grid_10["nearest"] = nearest

Check the result of the nearest interpolation on a map.

In [26]:
_ = grid_10.plot('nearest', legend=True)

You can see that the result is actually a Voronoi tessellation. If you
plot the original points on top, it is even clearer.

In [27]:
ax = grid_10.plot('nearest', legend=True)
_ = two_bed_homes.plot(ax=ax, color="red", markersize=1)

Nearest interpolation may be fine for some use cases, but it is not a
good interpolation method in general.

### K-nearest neighbours regression

Expanding the nearest method, which takes a single nearest neighbour and
allocates the values, you can use the K-nearest neighbours regression
(KNN) method. KNN takes into account multiple nearest neighbours and
interpolates the value based on all of them.

#### Uniform

The simple KNN option is to find $K$ nearest neighbours (say 10), treat
all equally (uniform weights), and obtain the interpolated value as a
mean of values these neighbours have. The implementation of KNN is
available in `scikit-learn`, so it has the API you are already familiar
with from the [Clustering and
regionalisation](../clustering/hands_on.qmd) section.

In [28]:
interpolation_uniform = neighbors.KNeighborsRegressor(
    n_neighbors=10, weights="uniform"
)

As with the clustering, use the `fit()` method to *train* the object.

In [29]:
interpolation_uniform.fit(
    homes_coordinates, two_bed_homes.price_lag
)

KNeighborsRegressor(n_neighbors=10) In a Jupyter environment, please rerun this cell to show the HTML representation or trust the notebook. On GitHub, the HTML representation is unable to render, please try loading this page with nbviewer.org.   KNeighborsRegressor ? Documentation for KNeighborsRegressor i Fitted KNeighborsRegressor(n_neighbors=10)

Once the model is ready, you can *predict* the values on the grid
coordinates.

In [30]:
price_on_grid = interpolation_uniform.predict(grid_coordinates)
price_on_grid

array([111.56773545, 139.93245582, 104.98715928, ..., 120.36697169,
       120.36697169, 120.36697169])

This is, again, a `numpy.ndarray` that is aligned and can be directly
set as a column.

In [31]:
grid_10["knn_uniform"] = price_on_grid

Check the result on a map.

In [32]:
_ = grid_10.plot("knn_uniform", legend=True)

This is already much better than the simple nearest join based on a
single neighbor but there are still a lot of artefacts in the areas
where you have only a few points far away from each other.

> **Using `KNeighborsRegressor` for the nearest join**
>
> You have probably figured out that you don’t need
> `scipy.interpolate.griddata` to do the nearest join if you have access
> to `sklearn.neighbors.KNeighborsRegressor`. With `n_neighbors=1`, the
> result should be the same. However, there are situations when only one
> is available, so it is good to know your options.

#### Distance-weighted

One way to mitigate the artefacts and take geography a bit more into the
equation is to use distance-weighted KNN regression. Instead of treating
each neighbour equally, no matter how far from the location of interest
they are, you can weigh the importance of each by distance, or to be
more precise, by the inverse of the distance. This ensures that points
that are closer and considered more important for the interpolation than
those that are further away.

In [33]:
interpolation_distance = neighbors.KNeighborsRegressor(
    n_neighbors=10, weights="distance"
)

The only difference is in the `weight` argument. The rest is the same.

In [34]:
interpolation_distance.fit(
    homes_coordinates, two_bed_homes.price_lag
)

KNeighborsRegressor(n_neighbors=10, weights='distance') In a Jupyter environment, please rerun this cell to show the HTML representation or trust the notebook. On GitHub, the HTML representation is unable to render, please try loading this page with nbviewer.org.   KNeighborsRegressor ? Documentation for KNeighborsRegressor i Fitted KNeighborsRegressor(n_neighbors=10, weights='distance')

Train the model, predict the values for the grid and assign to the
`GeoDataFrame`.

In [35]:
grid_10["knn_distance"] = interpolation_distance.predict(grid_coordinates)

If you look at the resulting map, you can see that most of the artefacts
are gone.

In [36]:
_ = grid_10.plot("knn_distance", legend=True)

### Distance band regression

Distance can be employed in another way as well. Instead of selecting
the neighbours from which the values are interpolated based on K-nearest
neighbours, you can select them based on distance. For example, find all
points in a radius of 1000 metres around a location of interest and draw
the interpolated value from them. You can also further weigh these
neighbours using the inverse distance. The code looks nearly identical.
Just use `neighbors.RadiusNeighborsRegressor` instead of
`neighbors.KNeighborsRegressor`.

In [37]:
interpolation_radius = neighbors.RadiusNeighborsRegressor(
    radius=1000, weights="distance"
)
interpolation_radius.fit(
    homes_coordinates, two_bed_homes.price_lag
)

grid_10["radius"] = interpolation_radius.predict(grid_coordinates)

/home/runner/micromamba/envs/sds/lib/python3.11/site-packages/sklearn/neighbors/_regression.py:505: UserWarning: One or more samples have no neighbors within specified radius; predicting NaN.
  warnings.warn(empty_warning_msg)

Check the result. The issue with sparsely populated areas on the map is
a bit different this time. When there is no neighbour in 1000m, the
model is not able to produce any prediction and returns `np.nan`. This
may be seen as an issue but it can actually be a strength of the model
as it is upfront with the issues caused by sparsity. Note that the model
warns you about this situation during the prediction phase.

In [38]:
_ = grid_10.plot("radius", legend=True, missing_kwds={'color': 'lightgrey'})

### Ordinary Kriging

The final method of this section is ordinary kriging. Kriging is based
on a linear combination of observations that are nearby, like all the
cases above, but the model is more complex and takes into account
geographical proximity, but also the spatial arrangement of observations
and the pattern of autocorrelation. As such, it can be seen as the most
robust of the presented options.

You will use the package `pyinterpolate` to do kriging. It requires all
input data in a single `numpy.ndarray` composed of coordinates and
values.

In [39]:
input_data = np.hstack(
    [homes_coordinates, two_bed_homes.price_lag.values.reshape(-1, 1)]
)
input_data

array([[3.26748646e+05, 6.74001683e+05, 2.07033397e+02],
       [3.24950724e+05, 6.73875598e+05, 1.54805935e+02],
       [3.26493725e+05, 6.72853904e+05, 1.43865293e+02],
       ...,
       [3.28513265e+05, 6.74048892e+05, 1.06875409e+02],
       [3.26840903e+05, 6.74767224e+05, 1.68848108e+02],
       [3.25415664e+05, 6.73345158e+05, 2.15847334e+02]])

The `input_data` is now an array `pyinterpolate` expects. The first step
is to build an experimental variogram based on the data and a couple of
parameters.

In [40]:
exp_semivar = pyinterpolate.build_experimental_variogram(
    input_array=input_data,
    step_size=100,
    max_range=5000,
)

The result can be plotted and explored using the `plot()` method. The
experimental variogram is a plot that shows how the semivariance between
pairs of sample points changes with distance. The variogram is
calculated by taking pairs of sample points and computing the
semivariance of the differences in their values at different distances.
It measures the degree of relationship between points at different
distances. Semivariance is half the variance of the differences in
values between pairs of points at a set distance.

In [41]:
exp_semivar.plot()

Next, you need to build a theoretical semivariogram based on the
experimental variogram.

In [42]:
semivar = pyinterpolate.build_theoretical_variogram(
    experimental_variogram=exp_semivar,
    model_name='linear',
    sill=exp_semivar.variance,
    rang=5000,
)

Again, you can plot the result. The theoretical variogram is a model or
a mathematical function that is fitted to the experimental variogram.

In [43]:
semivar.plot()

You can see that the linear model does not precisely follow the
experimental semivariances. Let’s try another option.

In [44]:
semivar_spherical = pyinterpolate.build_theoretical_variogram(
    experimental_variogram=exp_semivar,
    model_name='spherical',
    sill=exp_semivar.variance,
    rang=2500,
)

Let’s see if it is a bit better.

In [45]:
semivar_spherical.plot()

Now you are ready to use kriging to interpolate data on your grid.

In [46]:
ordinary_kriging = pyinterpolate.kriging(
    observations=input_data,
    theoretical_model=semivar_spherical,
    points=grid_coordinates.values,
    how="ok",
    no_neighbors=10,
    show_progress_bar=False,
)

The resulting `ordinary_kriging` is a numpy.ndarray with four columns
representing predicted value, variance error, x, and y. You can select
the first one and assign it as a column.

In [47]:
grid_10["ordinary_kriging"] = ordinary_kriging[:, 0]

And check the result.

In [48]:
_ = grid_10.plot("ordinary_kriging", legend=True)

Ordinary kriging looks great in dense areas but shows yet another type
of artefact in sparse areas. While there are ways to mitigate the issue
by changing the radius and other parameters of the model, it is worth
noting that the reliability of any interpolation method in sparsely
populated areas (in terms of the density of original points) is
questionable. Kriging has a method to indicate the error rate using the
variance error, which may help assess the issue. Variance error is the
second column of the `ordinary_kriging` array.

In [49]:
grid_10["variance_error"] = ordinary_kriging[:, 1]
_ = grid_10.plot("variance_error", legend=True)

You can see from the plot of variance error that anything further away
from existing points becomes fairly unreliable. You can, for example,
set the specific threshold of the variance error you think is acceptable
and treat all the other locations as *missing* or *unreliable*.

> **Check the effect of the theoretical semivariogram model**
>
> Explore the difference between kriging using linear and spherical
> models in theoretical semivariograms. What are the other options and
> their effects?

> **Additional reading**
>
> Have a look at the chapter [*Spatial Feature
> Engineering*](https://geographicdata.science/book/notebooks/12_feature_engineering.html?highlight=interpol#area-to-area-interpolation)
> from the Geographic Data Science with Python by @rey2023geographic to
> learn a bit more about areal interpolation or look at the [Areal
> Interpolation](https://gistbok.ucgis.org/bok-topics/2022-quarter-04/areal-interpolation)
> topic of The Geographic Information Science & Technology Body of
> Knowledge by @comber2022areal. The same source also contains a nice
> [explanation of
> kriging](https://gistbok.ucgis.org/bok-topics/kriging-interpolation)
> by @goovaerts2019kriging.